In [ ]:
# !pip install geojson
# !pip install folium
# !pip install geopandas
# !pip install pyogrio

import pandas as pd
import numpy as np
import geopandas as gpd
import folium

from shapely.geometry import LineString
import branca

import sys
import os
sys.path.append(os.path.abspath(os.path.join(os.getcwd(), '..')))
from utils_data import get_contours_city_simplifie, get_iris_contours_city
from utils_data import get_routing, get_df_OD_city, get_centroids_communes, restrict_area, get_traffic_demand_per_iris

In [2]:
# Paramètres externes
ratio_ev = 0.03 
conso_kwh_km = 0.2
code_insee = 44055
restricted_distance_km = 150
waiting_time_api = 0.1
# waiting_time_api = 1
file_iris = '../../data/IRIS/contours-iris.gpkg'
crs_angles = 'EPSG:4326'
crs_meters = 'EPSG:2154'

In [3]:
# files 
file_OD = '../../data/RP2020_MOBPRO_csv/FD_MOBPRO_2020.csv'
file_contours = '../../Data/communes-version-simplifiee.geojson'

In [4]:
export_file = f"../../data/processed/traffic_demand_per_iris_{code_insee}.geojson"

# Mobilité pendulaire

In [5]:
df_traffic_city = get_df_OD_city(file_OD, code_insee)

c:\Users\eliot\Documents\M2DS\Capstone\Code\utils.py:505: DtypeWarning: Columns (0,1,2,3,13,14,15,17,21,23,26,29,30,31) have mixed types. Specify dtype option on import or set low_memory=False.
  df_mob_full = pd.read_csv(file_OD, sep=';')
c:\Users\eliot\Documents\M2DS\Capstone\Code\utils.py:517: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_mob['transport_name'] = df_mob['TRANS'].apply(lambda x: dict_transport.get(x, 'default_value'))


In [6]:
# Loading and preprocessing of communes datasets
gdf_contours_city, geometry_contours_city = get_contours_city_simplifie(file_contours, code_insee)
gdf_contours_city['centroid'] = gdf_contours_city.geometry.centroid
centroid_city = gdf_contours_city.iloc[0].centroid
coord_centroid_city = [centroid_city.y, centroid_city.x]

C:\Users\eliot\AppData\Local\Temp\ipykernel_6684\1097055768.py:3: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  gdf_contours_city['centroid'] = gdf_contours_city.geometry.centroid


In [7]:
gdf_full = get_centroids_communes(file_contours, df_traffic_city, centroid_city)

In [8]:
gdf_full

code_commune  code_lieu_travail  cnt               centroid_hab  \
0           13005              44055    1    POINT (5.5637 43.29308)   
1           19031              44055    2   POINT (1.51988 45.14332)   
2           35066              44055    1  POINT (-1.70653 48.04524)   
3           35143              44055    1  POINT (-2.00922 48.24713)   
4           35236              44055    1  POINT (-2.08122 47.66047)   
..            ...                ...  ...                        ...   
96          85029              44055    1  POINT (-2.00433 46.98139)   
97          85047              44055    1   POINT (-1.8404 46.83536)   
98          85109              44055    1  POINT (-1.02234 46.86675)   
99          85163              44055    1  POINT (-2.26122 47.00888)   
100         92062              44055    1   POINT (2.23874 48.88404)   

                   centroid_lt  
0    POINT (-2.35483 47.29059)  
1    POINT (-2.35483 47.29059)  
2    POINT (-2.35483 47.29059)  
3    POINT (-2.35483 47.29059)  
4    POINT (-2.35483 47.29059)  
..                         ...  
96   POINT (-2.35483 47.29059)  
97   POINT (-2.35483 47.29059)  
98   POINT (-2.35483 47.29059)  
99   POINT (-2.35483 47.29059)  
100  POINT (-2.35483 47.29059)  

[101 rows x 5 columns]

#### People working in La Baule

In [9]:
# Create a base map centered on the mean of all centroids
m = folium.Map(location=coord_centroid_city, zoom_start=8)

# Add all habitation centroids (blue markers)
for _, row in gdf_full.iterrows():
    popup_text = f"Habitation - cnt: {row['cnt']}"
    # folium.Marker([lat_lt, lon_lt],  popup=popup_text, icon=folium.Icon(color="red")).add_to(m)
    lat_hab, lon_hab = row['centroid_hab'].y, row['centroid_hab'].x
    folium.Marker([lat_hab, lon_hab], popup=popup_text, icon=folium.Icon(color="blue")).add_to(m)

# Display the map
m

#### Reducing to a reasonable area 

In [10]:
gdf_filtered, restricted_area = restrict_area(gdf_full, restricted_distance_km)

In [11]:
# gdf_filtered
print(gdf_filtered.cnt.sum())
print(gdf_full.cnt.sum())

1139
1149


In [12]:
m = folium.Map(location=coord_centroid_city, zoom_start=8)

# Add all habitation centroids (blue markers)
for _, row in gdf_filtered.iterrows():
    popup_text = f"Habitation - cnt: {row['cnt']}"
    # folium.Marker([lat_lt, lon_lt],  popup=popup_text, icon=folium.Icon(color="red")).add_to(m)
    lat_hab, lon_hab = row['centroid_hab'].y, row['centroid_hab'].x
    folium.Marker([lat_hab, lon_hab], popup=popup_text, icon=folium.Icon(color='blue')).add_to(m)


folium.GeoJson(restricted_area, name="100 km Buffer", style_function=lambda x: {
    "fillColor": "blue",
    "color": "blue",
    "weight": 2,
    "fillOpacity": 0.2,
}).add_to(m)

# Display the map
m

### Estimer les routes prises pour venir

In [13]:
# Combiner les lignes qui correspondent aux mêmes paires OD
print(len(gdf_filtered))
gdf_filtered.head()

92


code_commune  code_lieu_travail  cnt               centroid_hab  \
2         35066              44055    1  POINT (-1.70653 48.04524)   
3         35143              44055    1  POINT (-2.00922 48.24713)   
4         35236              44055    1  POINT (-2.08122 47.66047)   
5         35238              44055    1  POINT (-1.68164 48.11158)   
6         35285              44055    1  POINT (-1.96884 47.76497)   

                 centroid_lt  
2  POINT (-2.35483 47.29059)  
3  POINT (-2.35483 47.29059)  
4  POINT (-2.35483 47.29059)  
5  POINT (-2.35483 47.29059)  
6  POINT (-2.35483 47.29059)

### Get routes and distances

In [14]:
gdf_filtered["routing"] = gdf_filtered.apply(lambda row: get_routing(row["centroid_hab"].coords[0], row["centroid_lt"].coords[0], delay=waiting_time_api), axis=1)
gdf_filtered["route"] = gdf_filtered["routing"].apply(lambda row: LineString(row["geometry"]["coordinates"]))
gdf_filtered["route"] = gpd.GeoSeries(gdf_filtered["route"], crs=crs_angles)
gdf_filtered["distance_km"] = gdf_filtered["routing"].apply(lambda row: row["distance"])
gdf_filtered.drop(columns=['routing'], inplace=True)
gdf_filtered = gdf_filtered.set_geometry('route')
gdf_filtered.head()

code_commune  code_lieu_travail  cnt               centroid_hab  \
2         35066              44055    1  POINT (-1.70653 48.04524)   
3         35143              44055    1  POINT (-2.00922 48.24713)   
4         35236              44055    1  POINT (-2.08122 47.66047)   
5         35238              44055    1  POINT (-1.68164 48.11158)   
6         35285              44055    1  POINT (-1.96884 47.76497)   

                 centroid_lt  \
2  POINT (-2.35483 47.29059)   
3  POINT (-2.35483 47.29059)   
4  POINT (-2.35483 47.29059)   
5  POINT (-2.35483 47.29059)   
6  POINT (-2.35483 47.29059)   

                                               route  distance_km  
2  LINESTRING (-1.70666 48.04522, -1.70655 48.044...     133.5853  
3  LINESTRING (-2.00612 48.24601, -2.00611 48.246...     161.1485  
4  LINESTRING (-2.083 47.66014, -2.0831 47.66003,...      79.1621  
5  LINESTRING (-1.68136 48.11159, -1.68137 48.111...     133.3113  
6  LINESTRING (-1.96845 47.764, -1.96829 47.76403...      94.1148

In [15]:
# Define the base map, centered on an average location
m = folium.Map(location=coord_centroid_city, zoom_start=8)  # Centered around France

# Ensure your dataframe is a GeoDataFrame
gdf = gpd.GeoDataFrame(gdf_filtered, geometry="route", crs=crs_angles)

# Add each route as a PolyLine on the map
for _, row in gdf.iterrows():
    if isinstance(row["route"], LineString):  # Check if geometry is valid
        folium.PolyLine(
            locations=[(lat, lon) for lon, lat in row["route"].coords],  # Reverse coords for Folium
            color="blue",
            weight=2.5,
            opacity=1
        ).add_to(m)

# Add all workplace centroids (green markers)
for _, row in gdf_filtered.iterrows():
    # if row['centroid_lt']:
    color='blue'
    lat_1, lon_1 = row['centroid_hab'].y, row['centroid_hab'].x
    lat_2, lon_2 = row['centroid_lt'].y, row['centroid_lt'].x
    folium.Marker([lat_1, lon_1], icon=folium.Icon(color=color)).add_to(m)
    folium.Marker([lat_2, lon_2], icon=folium.Icon(color=color)).add_to(m)

# Display the map
m

In [16]:
gdf_filtered.head()

code_commune  code_lieu_travail  cnt               centroid_hab  \
2         35066              44055    1  POINT (-1.70653 48.04524)   
3         35143              44055    1  POINT (-2.00922 48.24713)   
4         35236              44055    1  POINT (-2.08122 47.66047)   
5         35238              44055    1  POINT (-1.68164 48.11158)   
6         35285              44055    1  POINT (-1.96884 47.76497)   

                 centroid_lt  \
2  POINT (-2.35483 47.29059)   
3  POINT (-2.35483 47.29059)   
4  POINT (-2.35483 47.29059)   
5  POINT (-2.35483 47.29059)   
6  POINT (-2.35483 47.29059)   

                                               route  distance_km  
2  LINESTRING (-1.70666 48.04522, -1.70655 48.044...     133.5853  
3  LINESTRING (-2.00612 48.24601, -2.00611 48.246...     161.1485  
4  LINESTRING (-2.083 47.66014, -2.0831 47.66003,...      79.1621  
5  LINESTRING (-1.68136 48.11159, -1.68137 48.111...     133.3113  
6  LINESTRING (-1.96845 47.764, -1.96829 47.76403...      94.1148

### Get the demand for each zone

Idea: cars will recharge their full need in the city if they work or live there. 
* For each pair and zone, 
    * get the intersection with the city + the intersection zone and get the distance ratio
    * attribute to the zone the distance = distance ratio * full distance of the trip
    * multiply by the avg consumption to get the demand 

Problems:
* We consider that people working in La Baule will charge there (and not within their trip before)
* Should we not consider people living in La Baule but rather people living out and working here ? 
* Problem: considering the centroid, people only go through dept. No additional demand in the other zones of the city

In [17]:
gdf_contours_city

code              nom  \
31996  44055  Baule-Escoublac   

                                                geometry  \
31996  POLYGON ((-2.41697 47.2842, -2.39184 47.29429,...   

                        centroid  
31996  POINT (-2.35483 47.29059)

In [18]:
gdf_city_iris = get_iris_contours_city(file_iris, code_insee, crs = crs_angles)
gdf_demand_iris, gdf_final_od = get_traffic_demand_per_iris(gdf_filtered, gdf_contours_city, gdf_city_iris, ratio_ev, conso_kwh_km)

In [19]:
gdf_demand_iris

code_iris           nom_iris  \
0  440550101  La Baule les Pins   
1  440550102      Centre-Benoît   
2  440550103    Gare-Grand Clos   
3  440550104             Beslon   
4  440550105          Escoublac   
5  440550106           Le Guézy   

                                            geometry  demand_traffic_kWh  
0  MULTIPOLYGON (((-2.35133 47.27244, -2.35149 47...            0.000000  
1  MULTIPOLYGON (((-2.38127 47.27993, -2.38559 47...            0.000000  
2  MULTIPOLYGON (((-2.4273 47.27833, -2.42724 47....            0.000000  
3  MULTIPOLYGON (((-2.40491 47.28723, -2.40464 47...            0.000000  
4  MULTIPOLYGON (((-2.38977 47.30009, -2.38918 47...           52.770902  
5  MULTIPOLYGON (((-2.29702 47.3032, -2.2972 47.3...           70.929473

## Final plot

In [20]:
m = folium.Map(location=coord_centroid_city, zoom_start=12)

# Create a colormap based on the number of people in each carreau
min_demand = gdf_demand_iris['demand_traffic_kWh'].min()  # Minimum number of people
max_demand = gdf_demand_iris['demand_traffic_kWh'].max()  # Maximum number of people
colormap = branca.colormap.linear.YlOrRd_09.scale(min_demand, max_demand)  # Yellow to red color scale

# Add the colormap legend to the map
colormap.add_to(m)

# Ensure your dataframe is a GeoDataFrame
gdf = gpd.GeoDataFrame(gdf_filtered, geometry="route", crs="EPSG:4326")

# Add each route as a PolyLine on the map
for _, row in gdf.iterrows():
    if isinstance(row["route"], LineString):  # Check if geometry is valid
        folium.PolyLine(
            locations=[(lat, lon) for lon, lat in row["route"].coords],  # Reverse coords for Folium
            color="blue",
            weight=2.5,
            opacity=1
        ).add_to(m)

# Add all workplace centroids (green markers)
for _, row in gdf_final_od.iterrows():
    color = 'blue'
    lat_1, lon_1 = row['centroid_hab'].y, row['centroid_hab'].x
    
    # Extract the 'cnt' value
    cnt_value = row['cnt']
    
    # Add marker with popup
    folium.Marker(
        [lat_1, lon_1], 
        icon=folium.Icon(color=color), 
        popup=f"Nb voitures (th+ev): {cnt_value}"
    ).add_to(m)

# Iterate through each row in the GeoDataFrame and plot each feature
for _, row in gdf_demand_iris.iterrows():
    # Extract geometry and properties for each feature
    feature = row['geometry']
    demand = row['demand_traffic_kWh']  # Assuming this column exists
    nom = row['nom_iris']  # Assuming this column exists

    # Create a popup displaying the number of people
    text = f"{nom} : Additional demand={demand:.2f}kWh"
    popup = folium.Popup(text, max_width=300)
    
    # Style each feature based on the number of people
    folium.GeoJson(
        feature,
        name=f"Carreau {row.name}",
        popup=popup,
        style_function=lambda x, demand=demand: {
                'fillColor': colormap(demand),  # Color based on the number of people
                'color': 'black',  # Border color
                'weight': 2,  # Border width
                'fillOpacity': 0.7  # Fill opacity
            }
    ).add_to(m)
    
# Ajouter un contrôle des couches
folium.LayerControl().add_to(m)

# Afficher la carte
m

In [21]:
m = folium.Map(location=coord_centroid_city, zoom_start=12)

# Create a colormap based on the number of people in each carreau
min_demand = gdf_demand_iris['demand_traffic_kWh'].min()  # Minimum number of people
max_demand = gdf_demand_iris['demand_traffic_kWh'].max()  # Maximum number of people
colormap = branca.colormap.linear.YlOrRd_09.scale(min_demand, max_demand)  # Yellow to red color scale

# Add the colormap legend to the map
colormap.add_to(m)

# Iterate through each row in the GeoDataFrame and plot each feature
for _, row in gdf_demand_iris.iterrows():
    # Extract geometry and properties for each feature
    feature = row['geometry']
    demand = row['demand_traffic_kWh']  # Assuming this column exists
    nom = row['nom_iris']  # Assuming this column exists

    # Create a popup displaying the number of people
    text = f"{nom} : Additional demand={demand:.2f}kWh"
    popup = folium.Popup(text, max_width=300)
    
    # Style each feature based on the number of people
    folium.GeoJson(
        feature,
        name=f"Carreau {row.name}",
        popup=popup,
        style_function=lambda x, demand=demand: {
                'fillColor': colormap(demand),  # Color based on the number of people
                'color': 'black',  # Border color
                'weight': 2,  # Border width
                'fillOpacity': 0.7  # Fill opacity
            }
    ).add_to(m)
    
# Ajouter un contrôle des couches
folium.LayerControl().add_to(m)

# Afficher la carte
m

In [22]:
gdf_demand_iris.to_file(export_file, driver="GeoJSON")

In [23]:
gdf_demand_iris

code_iris           nom_iris  \
0  440550101  La Baule les Pins   
1  440550102      Centre-Benoît   
2  440550103    Gare-Grand Clos   
3  440550104             Beslon   
4  440550105          Escoublac   
5  440550106           Le Guézy   

                                            geometry  demand_traffic_kWh  
0  MULTIPOLYGON (((-2.35133 47.27244, -2.35149 47...            0.000000  
1  MULTIPOLYGON (((-2.38127 47.27993, -2.38559 47...            0.000000  
2  MULTIPOLYGON (((-2.4273 47.27833, -2.42724 47....            0.000000  
3  MULTIPOLYGON (((-2.40491 47.28723, -2.40464 47...            0.000000  
4  MULTIPOLYGON (((-2.38977 47.30009, -2.38918 47...           52.770902  
5  MULTIPOLYGON (((-2.29702 47.3032, -2.2972 47.3...           70.929473